# Hearing Aid Audio Quality Index (HAAQI)

In summary, HAAQI is an intrusive metric that requires the processed and reference signals. Both signal need to be amplified by the same prescripted gain formula. In CAD1 and ICASSP2024 challenges, this amplification was the NAL-R formula {cite}`byrne1986national`. In CAD2, the amplification corresponds to a multiband dynamic range compressor (MBC). 

As HAAQI performs a series of correlation between the reference and processed signals, it is expected that both signals have the same amplification. If they don't have the same amplifications the HAAQI score will be affected. Let's see this in an example.

:::{warning}
In Cadenza challenges, the amplification used for the reference signal is defined by the challenge and it is properly informed in the challenges description. The amplification used for the processed signal is defined by the participant. The baselines use the same amplifications for both signals but participants are free to change them if they believe a different amplification will result in a better signal for listener panel.
:::

The HAAQI function is located in `clarity/evaluator/haaqi/haaqi.py`.

The parameters are:
* processed_signal: the processed signal
* reference_signal: the reference signal
* processed_sample_rate: the sampling rate of the processed signal
* reference_sample_rate: the sampling rate of the reference signal
* audiogram: an audiogram object containing the centre frequencies and hearing loss levels in dB.
* ecualisation: a parameter that indicates if the reference signal already has the amplification applied or not.
* level1: level of the reference signal in dB SPL that corresponds to a signal RMS = 1.

:::{admonition} Google Colab
:class: warning
To run this tutorial on Google Colab, you will need install the PyClarity module by uncommenting and running the next cell.
:::

In [1]:
# print("Cloning git repo...")
# !git clone --depth 1 --branch v0.6.1 https://github.com/claritychallenge/clarity.git

# print("Installing the pyClarity...\n")
# %cd clarity
# %pip install -e .

# clear_output()
# print("Repository installed")

## Using MBC amplification

To learn more about our MBC, please read the [MBC documentation](../signal_processing/mbc).
The MBC is a non-linear amplification.

For our example:

* Reference signal: we will load a single-channel sample signal from librosa. 
* Processed signal: we will use the reference signal.
  
For the amplification, we wil use the MBC in both signals. 

As our processed signal will be equal to the reference signal, we will obtain the best possible score.

In [1]:
import librosa

reference, sample_rate = librosa.load(
   librosa.ex("brahms"),
   sr=None,
   duration=10,
   mono=False
)

Now, let's define the MBC

In [2]:
import numpy as np
from clarity.enhancer.multiband_compressor import MultibandCompressor
from clarity.utils.audiogram import Audiogram

# Seed the randomness
np.random.seed(2024)

# Create an Audiogram
audiogram = Audiogram(
    levels=[20, 20, 30, 40, 50, 60],
    frequencies=[250, 500, 1000, 2000, 4000, 8000]
)

# Construct the MBC
mbc = MultibandCompressor(
    crossover_frequencies=(
        np.array([250, 500, 1000, 2000, 4000]) * np.sqrt(2)
    ),
    sample_rate=sample_rate,
    compressors_params={
        "attack": [11, 11, 14, 13, 11, 11],
        "release": [80, 80, 80, 80, 100, 100],
        "threshold": -40,
        "ratio": 4,
        "makeup_gain": np.maximum((audiogram.levels - 20) / 3, 0),
        "knee_width": 0,
    }
)

And, apply it to the reference

In [3]:
# Compressed reference
compressed_reference_mbc = mbc(reference, return_bands=False)[0]

As we said, the processed signal will be equal to the reference

In [4]:
# Compressed processed
compressed_processed_mbc = mbc(reference, return_bands=False)[0]

Now compute the HAAQI. HAAQI operates at 24000 Hz. it is recommended to perform the downsampling to both signals before calling the metric.

In [5]:
from clarity.evaluator.haaqi import compute_haaqi
from clarity.utils.signal_processing import resample

compute_haaqi(
    processed_signal=resample(compressed_reference_mbc, sample_rate, 24000),
    reference_signal=resample(compressed_processed_mbc, sample_rate, 24000),
    processed_sample_rate=sample_rate,
    reference_sample_rate=sample_rate,
    audiogram=audiogram,
    equalisation=2, # reference already have amplification
    level1=65
)

0.9989994668188951

In [6]:
import IPython.display as ipd

print("Reference Signal")
ipd.display(ipd.Audio(reference, rate=24000))
print("Signal amplified using MBC")
ipd.display(ipd.Audio(compressed_reference_mbc, rate=24000))

Reference Signal


Signal amplified using MBC


# Appendix 

# Does HAAQI still work with a different amplification?

One can compute HAAQI using a different amplification, like NAL-R.
To illustrate this, we will run the previous example by replacing the MBC by the NAL-R prescription, which is a linear amplification.

In [8]:
import numpy as np
from clarity.enhancer.nalr import NALR

enhancer = NALR(
  nfir=220,
  sample_rate=sample_rate,
)
nalr_fir, _ = enhancer.build(audiogram)

In [9]:
# Apply the NAL-R amplification to each signal
compressed_processed = enhancer.apply(nalr_fir, reference)
compressed_reference = enhancer.apply(nalr_fir, reference)

# Compute HAAQI
compute_haaqi(
    processed_signal=resample(compressed_reference, sample_rate, 24000),
    reference_signal=resample(compressed_processed, sample_rate, 24000),
    processed_sample_rate=sample_rate,
    reference_sample_rate=sample_rate,
    audiogram=audiogram,
    equalisation=2, # reference already have amplification
    level1=65
)

0.9989998323792193

## Using different amplification

Let's see what happens if the amplifications use for the processed signal is not the same as the one used for the reference signal. The next computation is using:

* reference: MBC amplification
* processed: NAL-R amplification

In [12]:
# Compute HAAQI
compute_haaqi(
    processed_signal=compressed_processed,
    reference_signal=compressed_reference_mbc,
    processed_sample_rate=sample_rate,
    reference_sample_rate=sample_rate,
    audiogram=audiogram,
    equalisation=2, # reference already have amplification
    level1=65
)

0.38916995110013036

From the examples above, one can see that:
1. The best score is not exactly one but very close.
2. The amplification used doen't affect the performance of HAAQI as long one is using the same amplification for both signals.

Ok, if different amplifications can result in equaly good signals, why bother?
Well, let's hear the signals and then you can decide which one may work better.

In [13]:
import IPython.display as ipd

print("Reference Signal")
ipd.display(ipd.Audio(reference, rate=24000))
print("Signal amplified using MBC")
ipd.display(ipd.Audio(compressed_reference_mbc, rate=24000))
print("Signal amplified using NAL-R")
ipd.display(ipd.Audio(compressed_reference, rate=24000))

Reference Signal


Signal amplified using MBC


Signal amplified using NAL-R
